In [1]:
import tensorflow as tf
import numpy as np,sklearn,os,cv2,pandas
import tensorflow_hub as hub
import tensorflow_text as text
from tensorflow.keras import Model,layers


In [2]:
df=pandas.read_csv("./sentiment-emotion-labelled_Dell_tweets.csv")
df.head()

Unnamed: 0                   Datetime             Tweet Id  \
0           0  2022-09-30 23:29:15+00:00  1575991191170342912   
1           1  2022-09-30 21:46:35+00:00  1575965354425131008   
2           2  2022-09-30 21:18:02+00:00  1575958171423752203   
3           3  2022-09-30 20:05:24+00:00  1575939891485032450   
4           4  2022-09-30 20:03:17+00:00  1575939359160750080   

                                                Text        Username  \
0  @Logitech @apple @Google @Microsoft @Dell @Len...  ManjuSreedaran   
1  @MK_habit_addict @official_stier @MortalKombat...      MiKeMcDnet   
2  As @CRN celebrates its 40th anniversary, Bob F...        jfollett   
3  @dell your customer service is horrible especi...       daveccarr   
4  @zacokalo @Dell @DellCares @Dell give the man ...      heycamella   

  sentiment  sentiment_score       emotion  emotion_score  
0   neutral         0.853283  anticipation       0.587121  
1   neutral         0.519470           joy       0.886913  
2  positive         0.763791           joy       0.960347  
3  negative         0.954023         anger       0.983203  
4   neutral         0.529170         anger       0.776124

In [3]:
X,Y=df.Text,df.sentiment
Y.unique()

array(['neutral', 'positive', 'negative'], dtype=object)

In [4]:
Classes=['neutral', 'positive', 'negative']

In [5]:
X.shape,Y.shape

((24970,), (24970,))

In [6]:
X=np.array(X)
Y=np.array(Y)

In [15]:
bert_preprocess = hub.KerasLayer(
    "https://tfhub.dev/tensorflow/bert_en_uncased_preprocess/3")
bert_encoder = hub.KerasLayer(
    "https://tfhub.dev/tensorflow/bert_en_uncased_L-12_H-768_A-12/4")

In [8]:
New_Y=[]
for i,j in enumerate(Y):
    label=-2
    for k,l in enumerate(Classes):
        if l==j:
            label=k
            New_Y.append(label)
New_Y=np.array(New_Y)
New_Y.shape,X.shape
# 0 => Neutral and 1 => positive and 2 => negative

((24970,), (24970,))

In [9]:
from sklearn.model_selection import train_test_split as tts
X_train, X_test, y_train, y_test = tts(X,New_Y,test_size=0.2, random_state=42,shuffle=True)

In [10]:
X_train.shape,X_test.shape,y_train.shape,y_test.shape

((19976,), (4994,), (19976,), (4994,))

In [11]:
X_train[0],y_train[0]

("@Dell Apparently your company doesn't think that a swollen battery on a laptop that isn't even a year old is an issue. You are not honoring your warranty and overall putting me in the position where I am a walking fire hazard which as a customer for years now isn't right.",
 2)

In [12]:
textinput=layers.Input(shape=(),dtype=tf.string,name="text")
pre=bert_preprocess(textinput)
end=bert_encoder(pre)
# NN Layer
po=end["sequence_output"]  #["pooled_output"]
l=layers.Bidirectional(layers.GRU(128, return_sequences=True))(po)
l=layers.Bidirectional(layers.GRU(64, return_sequences=True))(l)
l=layers.Conv1D(64, 1, activation="relu", padding='same')(l)
l=layers.Flatten()(l)
l=layers.Dropout(0.2)(l)
l=layers.Dense(128,activation="relu",name="input")(l)
l=layers.Dense(64,activation="relu",name="in")(l)
l=layers.Dense(16,activation="relu",name="in1")(l)
l=layers.Dropout(0.2)(l)
l=layers.Dense(3,activation="softmax",name="output")(l) #[0.2,0.3,0.5] = 1
Model=tf.keras.Model(inputs=textinput,outputs=[l])


NameError: name 'bert_preprocess' is not defined

In [30]:
Model.compile("adam",loss="sparse_categorical_crossentropy",metrics=["accuracy"])
Model.summary()

In [31]:
hist=Model.fit(X_train,y_train,epochs=30,batch_size=80)

In [ ]:
Model.evaluate(X_test,y_test)

In [ ]:
Model.save("./Model_3_Bert_Uncase.h5")

In [ ]:
A=Model.predict(["you awake from a deep trance, step away from the phone to see your friends & family"])
a=np.argmax(A)
Classes[a],int(A[0][a]*100)